In [12]:
# Dependencies
from sklearn import tree
from sklearn.tree import export_graphviz
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import KBinsDiscretizer
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
import pandas as pd
import os
import numpy as np

In [13]:
# import csv and quick clean dataframe for modeling. Leave secondary comments for alternative column models
mv_df = pd.read_csv(os.path.join("..", "Resources", "movie_metadata_adjusted_revenue_threegenres_reviews.csv"))
mv_df['popularity'] = mv_df['popularity'].astype(int)
# mv_df['revenue'] = mv_df['revenue'].str.replace(',','').astype(float).astype(int)
# mv_df['popularity'] = mv_df['popularity'].astype(str)
# # mv_df['budget'] = mv_df['budget'].astype(str)
# # mv_df['vote_count'] = mv_df['vote_count'].astype(str)
mv_df['vote_average'] = mv_df['vote_average'].astype(str)
mv_df['revenue'] = mv_df['revenue'].str.replace(',','').astype(float).astype(int)
mv_df['top_critic_review_count'] = mv_df['top_critic_review_count'].astype(int)
mv_df['review_count'] = mv_df['review_count'].astype(int)
mv_df_final = mv_df.drop(columns={'title', 'release_date', 'runtime', 'first_genre',\
'second_genre', 'third_genre', 'Unnamed: 0'}, axis=1)

mv_df_final

budget  popularity     revenue vote_average  vote_count  \
0       6000000          41  1499126346          8.5        6024   
1      25000000          51    48899552          8.5        8358   
2      63000000          63   154791744          8.3        9678   
3      22000000          41   568672494          8.3        4436   
4       3000000          35   517964907          8.3        3001   
...         ...         ...         ...          ...         ...   
1094   25000000          24    86673943          4.8        1075   
1095  150000000           9   373412184          4.7        1180   
1096   57000000           9   169652635          4.7        1163   
1097  125000000          17   379498823          4.2        1447   
1098    4000000          10    56562409          4.1        1034   

      top_critic_review_count  review_count  star_power  
0                          24            82           1  
1                          18            63           1  
2                          36           153           1  
3                          22            84           1  
4                          13            59           1  
...                       ...           ...         ...  
1094                       20           111           0  
1095                       43           188           0  
1096                       21           112           1  
1097                       28            87           1  
1098                       37           132           1  

[1099 rows x 8 columns]

In [14]:
# set up data, target and feature_names variables for future use. Leave secondary values
# commented should we wish to run other columns
target = mv_df_final['vote_average']
# target = mv_df2['popularity']
data = mv_df_final.drop("vote_average", axis=1)
# data = mv_df2.drop("popularity", axis=1)
feature_names = data.columns
print(feature_names)

Index(['budget', 'popularity', 'revenue', 'vote_count',
       'top_critic_review_count', 'review_count', 'star_power'],
      dtype='object')


In [15]:
# setup rf model
rf = RandomForestClassifier(max_depth=2, random_state=0)
rf.fit(data, target)

/Users/brian.abbe/anaconda3/envs/Pythondata/lib/python3.6/site-packages/sklearn/ensemble/forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)


RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=2, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=10,
                       n_jobs=None, oob_score=False, random_state=0, verbose=0,
                       warm_start=False)

In [16]:
# bin the data with KBinsDiscretizer
enc = KBinsDiscretizer(n_bins=10, encode='ordinal')
enc.fit(data)
result = enc.transform(data)
result

/Users/brian.abbe/anaconda3/envs/Pythondata/lib/python3.6/site-packages/sklearn/preprocessing/_discretization.py:193: UserWarning: Bins whose width are too small (i.e., <= 1e-8) in feature 6 are removed. Consider decreasing the number of bins.
  'decreasing the number of bins.' % jj)


array([[0., 9., 9., ..., 2., 2., 1.],
       [2., 9., 0., ..., 2., 2., 1.],
       [5., 9., 2., ..., 4., 4., 1.],
       ...,
       [5., 1., 3., ..., 2., 3., 1.],
       [8., 7., 6., ..., 3., 2., 1.],
       [0., 2., 0., ..., 4., 3., 1.]])

In [17]:
# attempt to slice out the runtime and release_year columns from the binning. Alternatively, 
# drop those columns completely in cell two

# print(result[:,1:2])
# data.iloc[:,[1,2]] = result.iloc[:,[1,2]]
# data[:,2:3] = result[:,2:3]
# data[:,4:5] = result[:,4:5]
# data[:,6:7] = result[:,6:7]
# data[:,7] = result[:,7]
# # X[:,2:9] = result[:,2:9]
# data['budget'] = result['budget']

In [31]:
# rerun rf on binned data
rf2 = RandomForestClassifier(max_depth=3, random_state=0, n_estimators=100)
rf2.fit(data, target)
print(rf2.feature_importances_)

[0.1632802  0.12932232 0.15915536 0.21303491 0.12171392 0.13563993
 0.07785336]


In [32]:
# sort feature_importances with title in descending order
sorted(zip(rf2.feature_importances_, mv_df.title), reverse=True)

[(0.21303491026189222, "Schindler's List"),
 (0.16328020184225464, 'The Godfather'),
 (0.15915536120815973, 'Fight Club'),
 (0.13563993420928044, 'The Dark Knight'),
 (0.12932231633458394, 'The Shawshank Redemption'),
 (0.12171391908637326, "One Flew Over the Cuckoo's Nest"),
 (0.07785335705745575, 'Whiplash')]

In [33]:
# setup train_test_split
X_train, X_test, y_train, y_test = train_test_split(data, target, random_state=42)

In [34]:
# scale the data and get an accuracy score
scaler = StandardScaler()
scaler.fit(X_train)

rf2 = rf2.fit(X_train, y_train)
rf2.score(X_test, y_test)

0.09454545454545454

In [22]:
# generate a graphviz and save visual

estimator = rf2.estimators_[5]

export_graphviz(estimator, out_file='movie.dot', 
                feature_names = feature_names,
                class_names = target,filled=True,
                rounded = True, proportion = False)

# Convert to png using system command (requires Graphviz)
from subprocess import call
call(['dot', '-Tpng', 'movie.dot', '-o', 'movies.png', '-Gdpi=600'])

# Display in jupyter notebook
from IPython.display import Image
Image(filename = 'movies.png')